In [2]:
!unzip train_data.zip

Archive:  train_data.rar
  End-of-central-directory signature not found.  Either this file is not
  a zipfile, or it constitutes one disk of a multi-part archive.  In the
  latter case the central directory and zipfile comment will be found on
  the last disk(s) of this archive.
unzip:  cannot find zipfile directory in one of train_data.rar or
        train_data.rar.zip, and cannot find train_data.rar.ZIP, period.


In [3]:
!pip install peft datasets transformers[torch] accelerate -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.9/190.9 kB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 32.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 280.0/280.0 kB 34.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 19.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 18.2 MB/s eta 0:00:00


In [4]:
import os
import torch
import pathlib
import pandas as pd
from IPython.display import clear_output

In [5]:
ROOT_DIR = os.path.abspath(os.getcwd())
ROOT_DIR

'/content'

По факту можно написать

In [6]:
CHARACTER = "rachel"
model_type = "gpt2-large"  # 'gpt2', 'gpt2-medium', 'gpt2-large'

In [7]:
from transformers import AutoTokenizer
from transformers import pipeline
from transformers import TextDataset, DataCollatorForLanguageModeling
from transformers import Trainer, TrainingArguments,AutoModelWithLMHead

Training on monologues

In [8]:
tokenizer = AutoTokenizer.from_pretrained(model_type)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/666 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

In [9]:
block_size_ = 128

Define paths to training data

In [10]:
path_to_single_data = './train_data/en/single/'
train_path = path_to_single_data + f'train_{CHARACTER}_single.txt'
test_path = path_to_single_data + f'valid_{CHARACTER}_single.txt'
train_path, test_path

('./train_data/en/single/train_rachel_single.txt',
 './train_data/en/single/valid_rachel_single.txt')

Create datasets

In [11]:
def load_dataset(train_path,test_path,tokenizer):
    train_dataset = TextDataset(
          tokenizer=tokenizer,
          file_path=train_path,
          block_size=block_size_)

    test_dataset = TextDataset(
          tokenizer=tokenizer,
          file_path=test_path,
          block_size=block_size_)

    data_collator = DataCollatorForLanguageModeling(
        tokenizer=tokenizer, mlm=False,
    )
    return train_dataset,test_dataset,data_collator

train_dataset, test_dataset, data_collator = load_dataset(train_path, test_path, tokenizer)

/usr/local/lib/python3.10/dist-packages/transformers/data/datasets/language_modeling.py:53: FutureWarning: This dataset will be removed from the library soon, preprocessing should be handled with the 🤗 Datasets library. You can have a look at this example script for pointers: https://github.com/huggingface/transformers/blob/main/examples/pytorch/language-modeling/run_mlm.py
  warnings.warn(
Token indices sequence length is longer than the specified maximum sequence length for this model (270493 > 1024). Running this sequence through the model will result in indexing errors


In [12]:
!mkdir ./models

In [13]:
model = AutoModelWithLMHead.from_pretrained(model_type)
output_folder = f"./models/en_{model_type}_{CHARACTER}_mono"

/usr/local/lib/python3.10/dist-packages/transformers/models/auto/modeling_auto.py:1595: FutureWarning: The class `AutoModelWithLMHead` is deprecated and will be removed in a future version. Please use `AutoModelForCausalLM` for causal language models, `AutoModelForMaskedLM` for masked language models and `AutoModelForSeq2SeqLM` for encoder-decoder models.
  warnings.warn(


model.safetensors:   0%|          | 0.00/3.25G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

Define arguments for trainings

In [17]:
training_args = TrainingArguments(
    output_dir = output_folder,
    overwrite_output_dir=True, #overwrite the content of the output directory
    num_train_epochs=5, # number of training epochs
    learning_rate=0.00001,  # learning rate
    lr_scheduler_type="linear",
    per_device_train_batch_size=8, # batch size for training
    per_device_eval_batch_size=8,  # batch size for evaluation
    eval_steps = 200, # number of update steps between two evaluations
    save_steps = 200, # after # steps model is saved
    save_strategy = "steps",
    evaluation_strategy = "steps",
    dataloader_drop_last=True, # avoid an error with an incomplete batch
    fp16=False,
    save_total_limit = 1, # Only last 5 models are saved. Older ones are deleted.
    load_best_model_at_end=True,
    )

trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
)

In [18]:
trainer.train()

There were missing keys in the checkpoint model loaded: ['lm_head.weight'].


TrainOutput(global_step=1320, training_loss=1.2858209552186908, metrics={'train_runtime': 751.9269, 'train_samples_per_second': 14.051, 'train_steps_per_second': 1.755, 'total_flos': 5745102815232000.0, 'train_loss': 1.2858209552186908, 'epoch': 5.0})

In [19]:
trainer.save_model()

In [20]:
# The name of the task to train.
TASK_NAME = f"{model_type}_mono_en_{CHARACTER}"

# The output directory where the fine-tuned model and checkpoints will be written.
OUTPUT_DIR = f'{ROOT_DIR}/outputs/{TASK_NAME}/'
pathlib.Path(OUTPUT_DIR).mkdir(parents=True, exist_ok=True)

CONFIG_NAME = "config.json"
WEIGHTS_NAME = f"{TASK_NAME}_pytorch_model.bin"

In [21]:
def saver(model, OUTPUT_DIR, WEIGHTS_NAME):
    model_to_save = model.module if hasattr(model, 'module') else model  # Only save the model it-self

    # If we save using the predefined names, we can load using `from_pretrained`
    output_model_file = os.path.join(OUTPUT_DIR, WEIGHTS_NAME)
    output_config_file = os.path.join(OUTPUT_DIR, CONFIG_NAME)

    torch.save(model_to_save.state_dict(), output_model_file)
    model_to_save.config.to_json_file(output_config_file)

saver(model, OUTPUT_DIR, WEIGHTS_NAME)

In [22]:
path_to_dialogs_data = './train_data/en/replics/'
train_path = path_to_dialogs_data + f'train_{CHARACTER}_replics.txt'
test_path = path_to_dialogs_data + f'valid_{CHARACTER}_replics.txt'
train_path, test_path

('./train_data/en/replics/train_rachel_replics.txt',
 './train_data/en/replics/valid_rachel_replics.txt')

In [23]:
train_dataset, test_dataset, data_collator = load_dataset(train_path, test_path, tokenizer)

/usr/local/lib/python3.10/dist-packages/transformers/data/datasets/language_modeling.py:53: FutureWarning: This dataset will be removed from the library soon, preprocessing should be handled with the 🤗 Datasets library. You can have a look at this example script for pointers: https://github.com/huggingface/transformers/blob/main/examples/pytorch/language-modeling/run_mlm.py
  warnings.warn(


In [24]:
model = AutoModelWithLMHead.from_pretrained(output_folder)
final_output_folder = f"./models/en_{model_type}_{CHARACTER}_replics"

/usr/local/lib/python3.10/dist-packages/transformers/models/auto/modeling_auto.py:1595: FutureWarning: The class `AutoModelWithLMHead` is deprecated and will be removed in a future version. Please use `AutoModelForCausalLM` for causal language models, `AutoModelForMaskedLM` for masked language models and `AutoModelForSeq2SeqLM` for encoder-decoder models.
  warnings.warn(


In [25]:
training_args = TrainingArguments(
    output_dir = final_output_folder,
    overwrite_output_dir=True, #overwrite the content of the output directory
    num_train_epochs=5, # number of training epochs
    learning_rate=0.00001,  # learning rate
    lr_scheduler_type="linear",
    per_device_train_batch_size=6, # batch size for training
    per_device_eval_batch_size=6,  # batch size for evaluation
    eval_steps = 400, # number of update steps between two evaluations
    save_steps = 400, # after # steps model is saved
    save_strategy = "steps",
    evaluation_strategy = "steps",
    dataloader_drop_last=True, # avoid an error with an incomplete batch
    fp16=False,
    save_total_limit = 1, # Only last 5 models are saved. Older ones are deleted.
    load_best_model_at_end=True,
    )

trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
)

In [26]:
trainer.train()

There were missing keys in the checkpoint model loaded: ['lm_head.weight'].


TrainOutput(global_step=1990, training_loss=1.7659926218004083, metrics={'train_runtime': 776.6032, 'train_samples_per_second': 15.381, 'train_steps_per_second': 2.562, 'total_flos': 6495883296768000.0, 'train_loss': 1.7659926218004083, 'epoch': 5.0})

In [27]:
trainer.save_model()

In [28]:
# The name of the task to train.
TASK_NAME = f'{model_type}_mono_replics_en_{CHARACTER}'

# The output directory where the fine-tuned model and checkpoints will be written.
OUTPUT_DIR = f'{ROOT_DIR}/outputs/{TASK_NAME}/'
pathlib.Path(OUTPUT_DIR).mkdir(parents=True, exist_ok=True)

CONFIG_NAME = "config.json"
WEIGHTS_NAME = f"{TASK_NAME}_pytorch_model.bin"

saver(model, OUTPUT_DIR, WEIGHTS_NAME)

In [30]:
chef = pipeline('text-generation', model="./models/en_gpt2-large_rachel_replics", tokenizer=model_type)

In [ ]:
tmp = chef(f"<s>NOTFRIEND: Do you like Ross?\nRACHEL:")[0]['generated_text']
tmp = tmp[tmp.find(f"RACHEL: ") + len("RACHEL") + 2 : tmp.find('</s>')]
tmp

In [32]:
message1 = "Hi, Rachel! How are you?"
message2 = "Glad to hear it! Where are you going?"

In [44]:
tmp = chef(f"<s>NOTFRIEND: {message1}\nRACHEL:")[0]['generated_text']

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


In [45]:
tmp = tmp[tmp.find(f"RACHEL: ") + len("RACHEL") + 2 : tmp.find('</s>')]
tmp

'Oh, it’s not bad, it’s like, perfect. I’m sorry, I know we should be togethe'

In [64]:
message1 = "Hi, Rachel! How are you?"
text = f"NOTFRIEND: {message1}\nRACHEL:"
inpt = tokenizer.encode(text, return_tensors="pt")

In [65]:
out = model.generate(inpt.cuda(),
                    max_length=50,
                    repetition_penalty=5.0,
                    do_sample=True,
                    top_k=5,
                    top_p=0.95,
                    temperature=1)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


In [67]:
generated_text = tokenizer.decode(out[0])
generated_text = generated_text[generated_text.find(f"RACHEL: ") + len("RACHEL") + 2 : generated_text.find('</s>')]

In [68]:
log_msg = "Model generates reply {} for {}".format(generated_text, message1)
log_msg

"Model generates reply Oh God. I'm good. for Hi, Rachel! How are you?"